In [19]:
# IMPORT STATEMENTS

import sys
sys.path.append("/Users/rohan/public_html/Hegemon")
import StepMiner as smn
import HegemonUtil as hu
import re
import numpy as np
import scipy
import io
from scipy import io
import math
import itertools
from itertools import combinations 
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.backends.backend_pdf import PdfPages
import pandas as pd
import statsmodels.stats.proportion
import seaborn as sns
import scanpy as sc
import GEOparse
import os

%run ../moreprocessing.py

In [20]:
# Read excel files from GEO

expr = pd.DataFrame(pd.read_excel("GSE175839_Expression.xlsx", header=0))
cols = ["Gene_ID", "Name"]+[i for i in list(expr.columns) if ("read count" in i)]
expr = expr[cols]
expr = expr.rename(columns=lambda x: x.split(":")[0])
expr

Gene_ID        Name   A5   A8  A11  A12  A14   B7   B8   B9  \
0      ENSG00000000003      TSPAN6    6   14    0    9   12   10   16    9   
1      ENSG00000000005        TNMD    0    0    0    0    0    0    0    0   
2      ENSG00000000419        DPM1  513  486  192  465  583  433  462  471   
3      ENSG00000000457       SCYL3  227  226  143  187  564  320  361  391   
4      ENSG00000000460    C1orf112   62   46   41   42  134  155   91   88   
...                ...         ...  ...  ...  ...  ...  ...  ...  ...  ...   
20019  ENSG00000286239  AC093884.1    0    0    0    0    0    0    0    0   
20020  ENSG00000286261  AC022137.3    8    5    0    2    3    0    5    4   
20021  ENSG00000286264  AP001453.5    0    0    0    0    0    0    0    0   
20022  ENSG00000286265  AC007244.1    0    0    0    0    0    0    0    0   
20023  ENSG00000286268  AF196969.1    0    0    1    0    0    0    1    0   

       B10  B12  
0       19    8  
1        0    0  
2      431  606  
3      423  282  
4      227  101  
...    ...  ...  
20019    0    0  
20020    1    1  
20021    0    0  
20022    0    0  
20023    0    0  

[20024 rows x 12 columns]

In [21]:
# Fix headers with ih file

ih = pd.DataFrame(pd.read_csv("GSE175839-GPL11154-ih.txt", sep="\t", header=0))
gsm_dict = {ih["ClinicalHeader"][i].split(" ")[0]:ih["ArrayID"][i] for i in range(len(ih.index))}
gsm_dict["Gene_ID"] = "ProbeID"
expr = expr.rename(gsm_dict, axis=1)
expr

ProbeID        Name  GSM5348683  GSM5348684  GSM5348685  \
0      ENSG00000000003      TSPAN6           6          14           0   
1      ENSG00000000005        TNMD           0           0           0   
2      ENSG00000000419        DPM1         513         486         192   
3      ENSG00000000457       SCYL3         227         226         143   
4      ENSG00000000460    C1orf112          62          46          41   
...                ...         ...         ...         ...         ...   
20019  ENSG00000286239  AC093884.1           0           0           0   
20020  ENSG00000286261  AC022137.3           8           5           0   
20021  ENSG00000286264  AP001453.5           0           0           0   
20022  ENSG00000286265  AC007244.1           0           0           0   
20023  ENSG00000286268  AF196969.1           0           0           1   

       GSM5348686  GSM5348687  GSM5348688  GSM5348689  GSM5348690  GSM5348691  \
0               9          12          10          16           9          19   
1               0           0           0           0           0           0   
2             465         583         433         462         471         431   
3             187         564         320         361         391         423   
4              42         134         155          91          88         227   
...           ...         ...         ...         ...         ...         ...   
20019           0           0           0           0           0           0   
20020           2           3           0           5           4           1   
20021           0           0           0           0           0           0   
20022           0           0           0           0           0           0   
20023           0           0           0           1           0           0   

       GSM5348692  
0               8  
1               0  
2             606  
3             282  
4             101  
...           ...  
20019           0  
20020           1  
20021           0  
20022           0  
20023           0  

[20024 rows x 12 columns]

In [22]:
# Normalize and log transform

genes = expr.loc[:,["ProbeID", "Name"]]
cols = expr.columns

expr = expr.drop(['ProbeID', 'Name'], axis=1)
expr = sc.AnnData(expr.T)
sc.pp.normalize_total(expr, target_sum=1e6)
sc.pp.log1p(expr, base = 2)

expr = pd.DataFrame(expr.X)
expr = expr.T
expr.insert(0, "Name", genes["Name"])
expr.insert(0, "ProbeID", genes["ProbeID"])
expr.columns = cols
expr

/usr/local/lib/python3.6/dist-packages/anndata/_core/anndata.py:119: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)


ProbeID        Name  GSM5348683  GSM5348684  GSM5348685  \
0      ENSG00000000003      TSPAN6    0.551370    1.078785    0.000000   
1      ENSG00000000005        TNMD    0.000000    0.000000    0.000000   
2      ENSG00000000419        DPM1    5.350436    5.307837    4.223630   
3      ENSG00000000457       SCYL3    4.218048    4.244507    3.824760   
4      ENSG00000000460    C1orf112    2.538520    2.218644    2.255800   
...                ...         ...         ...         ...         ...   
20019  ENSG00000286239  AC093884.1    0.000000    0.000000    0.000000   
20020  ENSG00000286261  AC022137.3    0.696560    0.482574    0.000000   
20021  ENSG00000286264  AP001453.5    0.000000    0.000000    0.000000   
20022  ENSG00000286265  AC007244.1    0.000000    0.000000    0.000000   
20023  ENSG00000286268  AF196969.1    0.000000    0.000000    0.127101   

       GSM5348686  GSM5348687  GSM5348688  GSM5348689  GSM5348690  GSM5348691  \
0        0.757770    0.875107    0.830182    1.126455    0.779873    1.315915   
1        0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
2        5.197519    5.375926    5.116176    5.136084    5.267609    5.120619   
3        3.940622    5.329295    4.694496    4.791622    5.006693    5.094373   
4        2.078638    3.366617    3.706817    2.950383    3.001887    4.232418   
...           ...         ...         ...         ...         ...         ...   
20019    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
20020    0.206053    0.273261    0.000000    0.453918    0.399070    0.108893   
20021    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
20022    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
20023    0.000000    0.000000    0.000000    0.102928    0.000000    0.000000   

       GSM5348692  
0        0.663138  
1        0.000000  
2        5.498311  
3        4.430901  
4        3.064707  
...           ...  
20019    0.000000  
20020    0.101570  
20021    0.000000  
20022    0.000000  
20023    0.000000  

[20024 rows x 12 columns]

In [23]:
writeExprIdx(expr)

08-Jul-2022 13:29:33 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE175839 already exists. Skipping.
08-Jul-2022 13:29:33 INFO GEOparse - File already exist: using local version.
08-Jul-2022 13:29:33 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE175839/GSE175839_family.soft.gz: 
08-Jul-2022 13:29:33 DEBUG GEOparse - DATABASE: GeoMiame
08-Jul-2022 13:29:33 DEBUG GEOparse - SERIES: GSE175839
08-Jul-2022 13:29:33 DEBUG GEOparse - PLATFORM: GPL11154
08-Jul-2022 13:29:33 DEBUG GEOparse - SAMPLE: GSM5348683
08-Jul-2022 13:29:33 DEBUG GEOparse - SAMPLE: GSM5348684
08-Jul-2022 13:29:33 DEBUG GEOparse - SAMPLE: GSM5348685
08-Jul-2022 13:29:33 DEBUG GEOparse - SAMPLE: GSM5348686
08-Jul-2022 13:29:33 DEBUG GEOparse - SAMPLE: GSM5348687
08-Jul-2022 13:29:33 DEBUG GEOparse - SAMPLE: GSM5348688
08-Jul-2022 13:29:33 DEBUG GEOparse - SAMPLE: GSM5348689
08-Jul-2022 13:29:33 DEBUG GEOparse - SAMPLE: GSM5348690
08-Jul-2022 13:29:33 DEBU

Starting expr
Done writing expr
Starting make_idx
Done with make_idx


In [24]:
%run runmoreprocessing.py

Database ID NEU11
Dataset Name Yang 2021 Neutrophils
key macv:neu:
Configuration file (default /Users/rohan) 


08-Jul-2022 13:30:20 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE175839 already exists. Skipping.
08-Jul-2022 13:30:20 INFO GEOparse - File already exist: using local version.
08-Jul-2022 13:30:20 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE175839/GSE175839_family.soft.gz: 
08-Jul-2022 13:30:20 DEBUG GEOparse - DATABASE: GeoMiame
08-Jul-2022 13:30:20 DEBUG GEOparse - SERIES: GSE175839
08-Jul-2022 13:30:20 DEBUG GEOparse - PLATFORM: GPL11154
08-Jul-2022 13:30:20 DEBUG GEOparse - SAMPLE: GSM5348683
08-Jul-2022 13:30:20 DEBUG GEOparse - SAMPLE: GSM5348684
08-Jul-2022 13:30:20 DEBUG GEOparse - SAMPLE: GSM5348685
08-Jul-2022 13:30:20 DEBUG GEOparse - SAMPLE: GSM5348686
08-Jul-2022 13:30:20 DEBUG GEOparse - SAMPLE: GSM5348687
08-Jul-2022 13:30:20 DEBUG GEOparse - SAMPLE: GSM5348688
08-Jul-2022 13:30:20 DEBUG GEOparse - SAMPLE: GSM5348689
08-Jul-2022 13:30:20 DEBUG GEOparse - SAMPLE: GSM5348690
08-Jul-2022 13:30:20 DEBU

[NEU11]
name = Yang 2021 Neutrophils
expr = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE175839/GSE175839-GPL11154-expr.txt
index = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE175839/GSE175839-GPL11154-idx.txt
survival = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE175839/GSE175839-GPL11154-survival.txt
indexHeader = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE175839/GSE175839-GPL11154-ih.txt
info = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE175839/GSE175839-GPL11154-info.txt
key = macv:neu:
source = GSE175839
Write to file? y/n y


08-Jul-2022 13:30:30 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE175839 already exists. Skipping.
08-Jul-2022 13:30:30 INFO GEOparse - File already exist: using local version.
08-Jul-2022 13:30:30 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE175839/GSE175839_family.soft.gz: 
08-Jul-2022 13:30:30 DEBUG GEOparse - DATABASE: GeoMiame
08-Jul-2022 13:30:30 DEBUG GEOparse - SERIES: GSE175839
08-Jul-2022 13:30:30 DEBUG GEOparse - PLATFORM: GPL11154
08-Jul-2022 13:30:30 DEBUG GEOparse - SAMPLE: GSM5348683
08-Jul-2022 13:30:30 DEBUG GEOparse - SAMPLE: GSM5348684
08-Jul-2022 13:30:30 DEBUG GEOparse - SAMPLE: GSM5348685
08-Jul-2022 13:30:30 DEBUG GEOparse - SAMPLE: GSM5348686
08-Jul-2022 13:30:30 DEBUG GEOparse - SAMPLE: GSM5348687
08-Jul-2022 13:30:30 DEBUG GEOparse - SAMPLE: GSM5348688
08-Jul-2022 13:30:30 DEBUG GEOparse - SAMPLE: GSM5348689
08-Jul-2022 13:30:30 DEBUG GEOparse - SAMPLE: GSM5348690
08-Jul-2022 13:30:30 DEBU